# Inference Component to make predictions

In [125]:
import math
import glob
import argparse
from functools import partial
from pathlib import Path

import torch
import pandas as pd
from tqdm import tqdm
import numpy as np
import joblib
import yaml

from train_pure_segment import DATA_DIR_STR, prepare_model as prepare_agnostic_model
from train_segment_w_context import prepare_model as prepare_aware_model
from dataloader import YoutubeTestDataset, DataLoader, collate_test_segments
from telegram_tokens import BOT_TOKEN, CHAT_ID
from telegram_sender import telegram_sender

BATCH_SIZE = 32

def inverse_label_mapping(vocab_path="./data/segment_vocabulary.csv"):
    vocab = pd.read_csv(vocab_path)
    return {
        index: label for label, index in zip(vocab["Index"], vocab.index)
    }

DATA_DIR_STR = "data/Youtube8MData"
def collect_file_paths():
    return list(glob.glob(str(DATA_DIR_STR + "/test/*.tfrecord")))


def prepare_model(model_path):
    with open('y8m-2019-trained/segment/dbof-3_0_20191030-0608/config.yaml') as fin:
        config = yaml.safe_load(fin)
    state_dict = torch.load(str(model_path),map_location=torch.device('cpu'))
    if "context_base" in config:
        # context-aware model
        model = prepare_aware_model(config)
    else:
        # context-agnostic model
        model = prepare_agnostic_model(config)
    model.load_state_dict(state_dict)
    return model

model_paths = ['y8m-2019-trained/segment/dbof-3_0_20191030-0608/model.pth']

#@telegram_sender(token=BOT_TOKEN, chat_id=CHAT_ID, name="Inferencing")

test_ds = YoutubeTestDataset(
    collect_file_paths(), offset=0, device="cpu")
loader = DataLoader(
    test_ds, batch_size=BATCH_SIZE, num_workers=1,
    collate_fn=partial(
        collate_test_segments,
        return_vid=False),
    pin_memory=True)
#ref_indices = joblib.load("data/cache/ref_indices.jl")

Offset: 0


In [110]:
with torch.no_grad():
    models = []
    predictions = []
    for model_path in model_paths:
        target_path = f"data/cache/predictions/testpred.npy"
        if Path(target_path).exists():
            print("Skipping ", model_path)
            continue
        print(model_path)
        model = prepare_model(model_path)
        models.append(model.eval())
        predictions.append(np.memmap(
            target_path,
            "int16", mode="w+", shape=(433376, 1000)
        ))
    if not models:
        print("No eligible models found!")
    global_indices = np.zeros(433376, dtype="int8")
    cnt = 0
    for video_features, video_masks, segment_features, indices in tqdm(
            loader, total=int(math.ceil(433376 / BATCH_SIZE))):
        # shape(frames / 5, n_classes)
        n_segments = segment_features.shape[0]
        for i, model in enumerate(models):
            # value range 0 ~ 9999
            probs = np.round(torch.sigmoid(
                model(
                    video_features, video_masks, segment_features
                )
            ).cpu().numpy() * 9999, 0).astype("int16")
            predictions[i][cnt:cnt+n_segments] = probs
        global_indices[cnt:cnt+n_segments] = indices
        cnt += n_segments
    #assert np.array_equal(ref_indices, global_indices)

y8m-2019-trained/segment/dbof-3_0_20191030-0608/model.pth


  0%|                                                 | 0/13543 [00:00<?, ?it/s]/Users/vishnu/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
100%|███████████████████████████████████| 13543/13543 [1:11:03<00:00,  3.18it/s]


In [143]:
import glob
import joblib
import numpy as np
import pandas as pd

from tqdm import tqdm
from inference_memmap import collect_file_paths
from dataloader import YoutubeTestDataset, DataLoader, collate_test_segments

DATA_DIR_STR = "data/Youtube8MData"
def collect_file_paths():
    return list(glob.glob(str(DATA_DIR_STR + "/test/*.tfrecord")))

test_ds = YoutubeTestDataset(
        collect_file_paths(), offset=3, device="cpu",
        vocab_path="data/segment_vocabulary.csv"
        )
vid_mapping = {}
video_lengths = []
global_indices = np.zeros(1704348, dtype="int8")
global_vids = np.zeros(1704348, dtype="int32")

vidid_arr =[]
for i, (video_features, segment_row, index, vid) in tqdm(enumerate(test_ds), total=433376):
    video_lengths.append(video_features.size(0))
    global_indices[i] = index
    if vid not in vid_mapping:
        vid_mapping[vid] = len(vid_mapping)
    global_vids[i] = vid_mapping[vid]
    vidid_arr.append(vid)

joblib.dump(global_indices, "data/cache/ref_indices.jl")
joblib.dump(global_vids, "data/cache/ref_vids.jl")
joblib.dump(vid_mapping, "data/cache/vid_mapping.jl")

Offset: 3


100%|███████████████████████████████▉| 433358/433376 [00:18<00:00, 23873.33it/s]


['data/cache/vid_mapping.jl']

In [148]:
# Create an empty dictionary to store predictions
predictions_dict = {}

# Iterate over each segment and update the dictionary
for i in range(len(vidid_arr)):
    vid_id = vidid_arr[i]
    pred_value = vocab.iloc[np.argmax(predictions[0][i])]['Name']  # Adjust this based on your actual calculation
    if vid_id not in predictions_dict:
        predictions_dict[vid_id] = [pred_value]
    else:
        predictions_dict[vid_id].append(pred_value)

In [155]:
predictions_dict = {}
top_n = 5

# Iterate over each segment and update the dictionary
for i in range(len(vidid_arr)):
    vid_id = vidid_arr[i]
    
    # Get the indices of the top_n classes
    top_indices = np.argsort(predictions[0][i])[-top_n:][::-1]
    
    # Get the corresponding class names and values
    top_classes = [vocab.iloc[index]['Name'] for index in top_indices]
    top_values = 0.0001*predictions[0][i][top_indices]

    if vid_id not in predictions_dict:
        predictions_dict[vid_id] = [list(zip(top_classes, top_values))]
    else:
        predictions_dict[vid_id].append(list(zip(top_classes, top_values)))

In [157]:
vidid_arr


['wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'TxhO',
 'TxhO',
 

In [156]:
predictions_dict 

{'wYhO': [[('Stadium', 9.991),
   ('Goalkeeper (association football)', 9.799),
   ('Association football', 9.786),
   ('Arena', 9.177),
   ('Penalty kick (association football)', 8.991)],
  [('Stadium', 9.994),
   ('Goalkeeper (association football)', 9.726),
   ('Arena', 9.662),
   ('Association football', 9.448),
   ('Penalty kick (association football)', 8.616)],
  [('Stadium', 9.986),
   ('Goalkeeper (association football)', 9.93),
   ('Association football', 9.815),
   ('Penalty kick (association football)', 9.8),
   ('Kick (football)', 9.147)],
  [('Stadium', 9.997),
   ('Goalkeeper (association football)', 9.847),
   ('Arena', 9.795),
   ('Association football', 9.097),
   ('Kick (football)', 6.965)],
  [('Stadium', 9.983),
   ('Goalkeeper (association football)', 9.684000000000001),
   ('Arena', 9.226),
   ('Association football', 5.7010000000000005),
   ('Cricket', 5.214)],
  [('Stadium', 9.992),
   ('Arena', 9.571),
   ('Goalkeeper (association football)', 9.556000000000001)

In [149]:
# Print the dictionary
for vid_id, pred_values in predictions_dict.items():
    print(f'For vidid {vid_id}, the corresponding predictions are: {pred_values}')

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [142]:

for i in range(len):
    print(vocab.iloc[np.argmax(predictions[0][i])]['Name'])

Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Stadium
Concert
Stadium
Stadium
Stadium
Armour
Glasses
Armour
Armour
Armour
Rock climbing
Rock climbing
Armour
GameSpot
GameSpot
Armour
Armour
Sephiroth (Final Fantasy)
Armour
Armour
Armour
GameSpot
Dragon
Sword
GameSpot
Knife
Statue
Armour
Logo
Lawn
Logo
Classroom
TV4 (Sweden)
Christmas decoration
Scarf
T-shirt
TV4 (Sweden)
Coach (sport)
Rooster
Reborn doll
Bumblebee (Transformers)


In [144]:
vidid_arr

['wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'wYhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'xzhO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'qihO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'kMhO',
 'TxhO',
 'TxhO',
 

In [115]:
# Find the index of the first occurrence of 0
np_gb = np.array(global_indices)

# Find the indices where global_indices is equal to 0
indices_of_zero = np.where(np_gb == 0)[0]

# Get the subarray until the first occurrence of 0
if indices_of_zero.size > 0:
    index_of_first_zero = indices_of_zero[0]
    subarray = np_gb[:index_of_first_zero]
else:
    # If there are no occurrences of 0, take the entire array
    subarray = np_gb

print(len(subarray))

433358


In [123]:
global_indices[0:100]

array([ 6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22,
       23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39,
       40, 41, 42, 43, 44, 45, 46, 47, 48, 49,  6,  7,  8,  9, 10, 11, 12,
       13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28,  6,
        7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23,
       24, 25, 26, 27, 28, 29,  6,  7,  8,  9, 10, 11, 12, 13, 14],
      dtype=int8)